<a href="https://colab.research.google.com/github/nu-collab-notebook/CityData/blob/SetUp/CityData.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Set Up Environment**

In [1]:
import sys
from google.colab import drive
import ipywidgets as widgets
from ipywidgets import Dropdown, Button, Output, VBox

# Mount Google Drive and setup paths
drive.mount('/content/drive/')
sys.path.append("/content/drive/MyDrive/CityDataNotebook/")
from pythonScripts import start_up_manager, data_manager

# Store selected city name (this determins the datasets the notebook will work on)
city = start_up_manager.choose_city()


# Display UI
display(start_up_manager.build_ui(city))
# Load city config
config = data_manager.load_city_config(city)

Mounted at /content/drive/


Successfully loaded config for Dundee


# **Routing test example**

**Please Add two markers (allow time between re-positioning)**

In [2]:
from ipywidgets import Button, VBox
from pythonScripts import marker_manager, map_renderer, data_manager

# Load city config
config = data_manager.load_city_config(city)

# Render the map with boundary
marker_map = map_renderer.render_map(config, "b_cityBoundry_path")

# Add marker cluster layer
marker_map.add_layer(marker_manager.marker_cluster)

# UI Buttons for adding/removing markers
add_marker_button = Button(description="Add Marker", button_style='info')
add_marker_button.on_click(lambda b: marker_manager.add_marker(marker_map, city))

delete_marker_button = Button(description="Delete Selected", button_style='danger')
delete_marker_button.on_click(lambda b: marker_manager.delete_selected_marker(marker_map))

# Click event to finalize marker placement
marker_map.on_interaction(lambda **kwargs: marker_manager.confirm_marker_placement(marker_map, **kwargs))

# Display marker controls and map
display(marker_map)
display(VBox([add_marker_button, marker_manager.marker_list, delete_marker_button]))
display(marker_manager.marker_output)


Successfully loaded config for Dundee


Map(center=[56.476401691737124, -2.9620267318538933], controls=(ZoomControl(options=['position', 'zoom_in_text…

Output()

Only driving routes seem to function atm. to display a route between the two above markers press the green button bellow.

In [ ]:
from ipywidgets import Dropdown, Button, VBox
from pythonScripts import route_analyser, marker_manager

global_latest_route = None
global_latest_transport_mode = "driving"

transport_selector = Dropdown(
    options={"Driving": "driving", "Walking": "foot", "Cycling": "bike"},
    value="driving",
    description="Transport:",
)

route_output  = route_analyser.route_output

def create_route():
    """ Generates and stores a route using the selected transport mode. """
    global global_latest_route, global_latest_transport_mode
    global_latest_transport_mode = transport_selector.value
    global_latest_route = route_analyser.generate_route(city, global_latest_transport_mode, marker_manager.marker_locations)

    if global_latest_route:
        print("Route successfully stored in global_latest_route.")
    else:
        print("Route generation failed.")

# Button to generate route
route_button = Button(description="Create Route", button_style='success')
route_button.on_click(lambda b: create_route())

display(VBox([transport_selector, route_button, route_output]))


Route successfully stored in global_latest_route.


Select from the list to display available location boundaries. You can also check if the above route intersects with any of them.

In [ ]:
from ipywidgets import Dropdown, Button, VBox
from pythonScripts import map_renderer, intersection_checker, route_analyser, marker_manager

config = data_manager.load_city_config(city)

boundary_options = {key: key for key in dir(config) if key.startswith("b_")}
boundary_selector = Dropdown(
    options=boundary_options,
    value="b_cityBoundry_path",
    description="Boundary:",
)
print("city")
print(city)

boundary_output = Output()

def update_boundary_map():
    """ Updates the displayed boundary map. """
    with boundary_output:
        boundary_output.clear_output()
        config = data_manager.load_city_config(city)
        if config:
            display(map_renderer.render_map(config, boundary_selector.value))
        else:
            print("Error: No valid city was selected.")

def check_route_intersection():
    """ Checks if the current route intersects with the selected boundary. """
    with boundary_output:

        boundary_output.clear_output()

        if global_latest_route is None:
            print("No valid route found. Please generate a route first.")
            return

        print("🔄 Checking for intersections...")
        intersection_checker.check_intersection(city, boundary_selector.value, global_latest_route)

# Buttons to update the boundary and check intersections
boundary_button = Button(description="Show Boundary", button_style='primary')
boundary_button.on_click(lambda b: update_boundary_map())

intersection_button = Button(description="Check Against Route", button_style='warning')
intersection_button.on_click(lambda b: check_route_intersection())

display(VBox([boundary_selector, boundary_button, intersection_button, boundary_output]))


Successfully loaded config for Dundee
city
Dundee


#**Testing Config and CSV File**

In [ ]:
# print out the contents of the dataset ( dummy data just to test access)
import pandas as pd
# display config variables

print("City Name:", config.CITY_NAME)
print("Dataset Path:", config.DATASET_PATH)

data_path = config.DATASET_PATH
df = pd.read_csv(data_path)
df.head()



City Name: dundee
Dataset Path: /content/drive/MyDrive/CityDataNotebook/data/dundee/dundee_dataset.csv


Post Code  Number Of Houses
0   DD1 1AD                 2
1   DD1 2AD                 3
2   DD3 3AD                 4